In [1]:
%load_ext autoreload
%autoreload 2
import os
import sys
import numpy as np
import pandas as pd
import xarray as xr
from os.path import join as pjoin
from tqdm import tqdm
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import pingouin as pg
from scipy.stats import pearsonr, zscore, spearmanr

sys.path.append("../..")
import circletrack_behavior as ctb
import circletrack_neural as ctn
import plotting_functions as pf
import place_cells as pc 

/home/austinbaggetta/.conda/envs/calcium/lib/python3.10/site-packages/outdated/utils.py:14: OutdatedPackageWarning: The package pingouin is out of date. Your version is 0.5.2, the latest is 0.5.3.
Set the environment variable OUTDATED_IGNORE=1 to disable these warnings.
  return warn(


In [2]:
## Set parameters
behavior_path = '../../../MultiCon_AfterHours/'
fig_path = '../../../MultiCon_AfterHours/MultiCon_EEG1/intermediate_figures/'
num_experiments = 2 + 1 ## change first value since np.arange is not inclusive
experiment_list = ['MultiCon_EEG{}'.format(x) for x in np.arange(1, num_experiments)]
session_dict = {'mc_EEG1_01': ['A1', 'A2', 'A3', 'A4', 'A5', 'B1', 'B2', 'B3', 'B4', 'B5',
                               'C1', 'C2', 'C3', 'C4', 'C5', 'D1', 'D2', 'D3', 'D4', 'D5'],
                'mc_EEG1_02': ['A1', 'A2', 'A3', 'A4', 'A5', 'B1', 'B2', 'B3', 'B4', 'B5',
                               'C1', 'C2', 'C3', 'C4', 'C5', 'A2_1', 'A2_2', 'A2_3', 'A2_4', 'A2_5'],
                'mc_EEG2_02': ['A1', 'A2', 'A3', 'A4', 'A5', 'B1', 'B2', 'B3', 'B4', 'B5',
                               'C1', 'C2', 'C3', 'C4', 'C5', 'A2_1', 'A2_2', 'A2_3', 'A2_4', 'A2_5']}

In [3]:
## Calculate lick accuracy, dprime metrics during non-probe
experiment_pc = {}
experiment_pc_trial = {}
experiment_sdt = {}
experiment_probe = {}
for experiment in experiment_list:
    bpath = pjoin(behavior_path, experiment)
    bpath = pjoin(bpath, 'output/behav')
    mouse_pc = {}
    mouse_pc_trial = {}
    mouse_sdt = {}
    mouse_probe = {}
    for mouse in os.listdir(bpath):
        path = pjoin(bpath, mouse)
        percent_correct = {}
        percent_correct_trials = {}
        sdt_metrics = {}
        probe_metrics = {}
        for session in np.arange(0, len(session_dict[mouse])):
            behav = pd.read_feather(pjoin(path, '{}_{}.feat'.format(mouse, session_dict[mouse][session])))
            behav_nonprobe = behav.loc[~behav['probe']]
            behav_probe = behav[behav['probe']]
            reward_one, reward_two = np.unique(behav['reward_one'])[0], np.unique(behav['reward_two'])[0]
            forward_trials, reverse_trials = ctb.get_forward_reverse_trials(behav)
            forward_df = behav.loc[(behav['trials'].isin(forward_trials))]
            forward_df = forward_df.loc[~forward_df['probe']]
            ## Percent correct licking
            pc = ctb.lick_accuracy(behav_nonprobe, port_one=reward_one, port_two=reward_two, by_trials=False)
            pc_trials = ctb.lick_accuracy(forward_df, port_one=reward_one, port_two=reward_two, by_trials=True)
            pc_probe = ctb.lick_accuracy(behav_probe, port_one=reward_one, port_two=reward_two, by_trials=False)
            percent_correct[session] = pc
            percent_correct_trials[session] = pc_trials
            probe_metrics[session] = pc_probe
            ## dprime, correct rejection, hit rate
            metrics = ctb.dprime_metrics(forward_df, reward_one, reward_two, reward_index='one', forward_reverse='forward')
            sdt_metrics[session] = metrics
        mouse_pc[mouse] = percent_correct
        mouse_pc_trial[mouse] = percent_correct_trials
        mouse_sdt[mouse] = sdt_metrics
        mouse_probe[mouse] = probe_metrics
    experiment_pc[experiment] = mouse_pc
    experiment_pc_trial[experiment] = mouse_pc_trial
    experiment_sdt[experiment] = mouse_sdt
    experiment_probe[experiment] = mouse_probe

/media/caishuman/csstorage3/Austin/CircleTrack/CircleTrackAnalysis/MultiCon_AfterHours/analysis/../../circletrack_behavior.py:1026: RuntimeWarning: invalid value encountered in scalar divide
  percent_correct.append(((count_licks['first_licks'][(count_licks['lick_port'] == port_one) | (count_licks['lick_port'] == port_two)].dropna().sum()) /
/media/caishuman/csstorage3/Austin/CircleTrack/CircleTrackAnalysis/MultiCon_AfterHours/analysis/../../circletrack_behavior.py:1026: RuntimeWarning: invalid value encountered in scalar divide
  percent_correct.append(((count_licks['first_licks'][(count_licks['lick_port'] == port_one) | (count_licks['lick_port'] == port_two)].dropna().sum()) /
/media/caishuman/csstorage3/Austin/CircleTrack/CircleTrackAnalysis/MultiCon_AfterHours/analysis/../../circletrack_behavior.py:1026: RuntimeWarning: invalid value encountered in scalar divide
  percent_correct.append(((count_licks['first_licks'][(count_licks['lick_port'] == port_one) | (count_licks['lick_port'] 

In [52]:
## Percent correct data non_probe
accuracy = pd.DataFrame()
for experiment in experiment_pc:
    for mouse in experiment_pc[experiment]:
        if mouse == 'mc_EEG2_01':
            next
        else:
            df = pd.DataFrame(experiment_pc[experiment][mouse], index=[0]).T.rename(columns={0: 'percent_correct'})
            df.insert(0, 'mouse', mouse)
            df.insert(1, 'day', [x for x in np.arange(1, 21)])
            accuracy = pd.concat([accuracy, df], axis=0, ignore_index=True)

# probe_accuracy = pd.DataFrame()
# for experiment in experiment_probe:
#     for mouse in experiment_probe[experiment]:
#         if mouse == 'mc_EEG2_01':
#             next
#         else:
#             df = pd.DataFrame(experiment_probe[experiment][mouse], index=[0]).T.rename(columns={0: 'percent_correct'})
#             df.insert(0, 'mouse', mouse)
#             df.insert(1, 'day', [x for x in np.arange(1, 21)])
#             probe_accuracy = pd.concat([probe_accuracy, df], axis=0, ignore_index=True)

fig = pf.plot_behavior_across_days(accuracy, x_var='day', y_var='percent_correct', groupby_var=['day'], 
                                   font_size=22, x_title='Day', y_title='Lick Accuracy (%)', template='simple_white', expert_line=False,
                                   transition_color=['black', 'black', 'black'])
fig.update_layout(title={
    'text': 'Lick Accuracy',
    'y':0.9,
    'x':0.5,
    'xanchor': 'center',
    'yanchor': 'top'})
fig.update_xaxes(dtick=2) 
fig.update_yaxes(range=[0, 100])
fig.show()
fig.write_image(pjoin(fig_path, 'lick_accuracy.png'))

In [ ]:
## Plot starting from B for R01_AD
accuracy_gt5 = accuracy[accuracy['day'] > 5]
accuracy_gt5['day'] = accuracy_gt5['day'] - 5
fig = pf.plot_behavior_across_days(accuracy_gt5, x_var='day', y_var='percent_correct', groupby_var=['day'],
                                   font_size=22, x_title='Day', y_title='Percent Correct (%)', template='simple_white', expert_line=False,
                                   transition_color=['black', 'black'], plot_transitions=[5.5, 10.5])
fig.update_layout(title={
    'text': 'Lick Accuracy',
    'y':0.9,
    'x':0.5,
    'xanchor': 'center',
    'yanchor': 'top'})
fig.update_xaxes(dtick=2) 
fig.update_yaxes(range=[0, 100])
fig.show()
fig.write_image(pjoin(fig_path, 'lick_accuracy_gt5.png'))

In [ ]:
## Get days to 75% for each mouse
days_to_dict = {'mouse': ['mc_EEG1_01', 'mc_EEG1_02', 'mc_EEG2_02'],
                'A': [5, 4, 5],
                'B': [5, 5, 5],
                'C': [5, 2, 2],
                'D': [2, 1, 2]}
df = pd.DataFrame(days_to_dict)
melt_df = df.melt(id_vars=['mouse'], 
                  value_vars=['A', 'B', 'C', 'D'],
                  var_name='context',
                  value_name='days_to')
avg_days = melt_df.groupby(['context'], as_index=False, sort=False).agg({'days_to': ['mean', 'sem']})
avg_days_df = pd.concat((avg_days['context'], avg_days['days_to']), axis=1)
## Plot
fig = pf.custom_graph_template(x_title='', y_title='Days to Criteria', titles=['Young Mice'])
fig.add_trace(go.Scatter(x=avg_days_df['context'], y=avg_days_df['mean'],
                            mode='lines+markers',
                            error_y=dict(type='data', array=avg_days_df['sem']),
                            line=dict(color='turquoise')))
fig.update_yaxes(dtick=2, range=[0, 10])
fig.show()

In [ ]:
## Get performance drop for each mouse
performance_drop = ctb.performance_drop(accuracy, day_list=[5, 10, 15], replace=True)
performance_drop = performance_drop.replace({5: 'A to B', 10: 'B to C', 15: 'C to D'})
avg_drop = performance_drop.groupby(['day'], as_index=False).agg({'drop': ['mean', 'sem']})
avg_drop_df = avg_drop['drop']
avg_drop_df.insert(0, 'day', avg_drop['day'])
## Plot fig
fig = pf.custom_graph_template(x_title='', y_title='Performance Difference (%)')
fig.add_trace(go.Bar(x=avg_drop_df['day'], y=avg_drop_df['mean'],
                     error_y=dict(type = 'data', array=avg_drop_df['sem'], thickness = 2.5, width = 10),
                     marker_color='darkgrey', marker_line_color='black',
                     marker_line_width=2, showlegend=False, width=0.5))
for mouse in np.unique(performance_drop['mouse']):
    sub_data = performance_drop[performance_drop['mouse'] == mouse]
    fig.add_trace(go.Scatter(x=sub_data['day'], y=sub_data['drop'], mode='lines', 
                                marker_color='black', showlegend=False))
fig.show()
fig.write_image(pjoin(fig_path, 'performance_drop.png'))

In [ ]:
pg.homoscedasticity(data=performance_drop, dv='drop', group='day')

In [ ]:
performance_drop.anova(dv='drop', between='day', detailed=True)

In [ ]:
print(f'n: {pg.power_anova(eta_squared=0.45, k=3, power=0.9)}')

In [ ]:
performance_drop.pairwise_tukey(dv='drop', between='day')

In [7]:
## Calculate percent correct during probe
experiment_pc_probe = {}
for experiment in experiment_list:
    bpath = pjoin(behavior_path, experiment)
    bpath = pjoin(bpath, 'output/behav')
    mouse_pc = {}
    for mouse in os.listdir(bpath):
        path = pjoin(bpath, mouse)
        percent_correct = {}
        for session in np.arange(0, len(session_dict[mouse])):
            behav = pd.read_feather(pjoin(path, '{}_{}.feat'.format(mouse, session_dict[mouse][session])))
            reward_one, reward_two = np.unique(behav['reward_one'])[0], np.unique(behav['reward_two'])[0]
            probe_behav = behav.loc[behav['probe']]
            pc = ctb.probe_lick_accuracy(probe_behav, port_one=reward_one, port_two=reward_two)
            percent_correct[session] = pc
        mouse_pc[mouse] = percent_correct
    experiment_pc_probe[experiment] = mouse_pc

/media/caishuman/csstorage3/Austin/CircleTrack/CircleTrackAnalysis/MultiCon_AfterHours/analysis/../../circletrack_behavior.py:994: RuntimeWarning:

invalid value encountered in scalar divide

/media/caishuman/csstorage3/Austin/CircleTrack/CircleTrackAnalysis/MultiCon_AfterHours/analysis/../../circletrack_behavior.py:994: RuntimeWarning:

invalid value encountered in scalar divide

/media/caishuman/csstorage3/Austin/CircleTrack/CircleTrackAnalysis/MultiCon_AfterHours/analysis/../../circletrack_behavior.py:994: RuntimeWarning:

invalid value encountered in scalar divide



In [14]:
## Percent correct probe
accuracy_probe = pd.DataFrame()
for experiment in experiment_pc_probe:
    for mouse in experiment_pc_probe[experiment]:
        if mouse == 'mc_EEG2_01':
            next
        else:
            df = pd.DataFrame(experiment_pc_probe[experiment][mouse], index=[0]).T.rename(columns={0: 'percent_correct'})
            df.insert(0, 'mouse', mouse)
            df.insert(1, 'day', [x for x in np.arange(1, 21)])
            accuracy_probe = pd.concat([accuracy_probe, df], axis=0, ignore_index=True)
# accuracy_probe = accuracy_probe[accuracy_probe['day'] > 1]
fig = pf.plot_behavior_across_days(accuracy_probe, x_var='day', y_var='percent_correct', groupby_var=['day'], titles=['Lick Accuracy During Probe'],
                                   font_size=22, x_title='Day', y_title='Percent Correct (%)', template='simple_white', expert_line=False,
                                   transition_color=['black', 'black', 'black'])
fig.update_xaxes(dtick=2)                                   
fig.show()
# fig.write_image(pjoin(fig_path, 'probe_accuracy.png'))

In [49]:
first_last = accuracy_probe[(accuracy_probe['day'] == 1) | (accuracy_probe['day'] == 5) | (accuracy_probe['day'] == 6) | (accuracy_probe['day'] == 10) | (accuracy_probe['day'] == 11) | 
                            (accuracy_probe['day'] == 15) | (accuracy_probe['day'] == 16) | (accuracy_probe['day'] == 20)]
first_last['day_type'] = ['first', 'last'] * 12
first_last['session'] = ['A', 'A', 'B', 'B', 'C', 'C', 'D', 'D'] * 3
## Probe accuracy on first and last day for B, C, D
context_list = ['A', 'B', 'C', 'D']
avg_combined = first_last.groupby(['day_type', 'session'], as_index=False).agg({'percent_correct': ['mean', 'sem']})

## Plot 
fig = pf.custom_graph_template(x_title='', y_title='', width=800, rows=1, columns=len(context_list), 
                               font_size=22, titles=['A', 'B', 'C', 'D'], shared_x=True, shared_y=True)
for idx, session in enumerate(context_list):
    plot_data = avg_combined[avg_combined['session'] == session]
    fig.add_trace(go.Scatter(x=plot_data['day_type'], y=plot_data['percent_correct']['mean'],
                                error_y=dict(type='data', array=plot_data['percent_correct']['sem'], thickness=1.5, width=8), 
                                line_color='turquoise', showlegend=False), row=1, col=idx+1)
    fig.add_hline(y=25, line_width=1, line_dash='dash', line_color='darkgrey', opacity=1)
fig.update_yaxes(title='Probe Accuracy (%)', col=1)
fig.show()
fig.write_image(pjoin(fig_path, 'first_last_probe_accuracy.png'))

/tmp/ipykernel_10173/3968899824.py:3: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/tmp/ipykernel_10173/3968899824.py:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [ ]:
## d' across days
dprime_df = pd.DataFrame()
for experiment in experiment_pc:
    for mouse in experiment_pc[experiment]:
        if mouse == 'mc_EEG2_01':
            next
        else:
            df = pd.DataFrame(experiment_sdt[experiment][mouse]).T
            d = []
            for idx in np.arange(0, len(df['dprime'])):
                d.append(np.nanmean(df['dprime'][idx]))
            dprime = pd.DataFrame(d).rename(columns={0: 'dprime'})
            dprime.insert(0, 'mouse', mouse)
            dprime.insert(1, 'day', [x for x in np.arange(1, 21)])
            dprime_df = pd.concat([dprime_df, dprime], axis=0, ignore_index=True)

fig = pf.plot_behavior_across_days(dprime_df, x_var='day', y_var='dprime', groupby_var=['day'], titles=[''],
                                   x_title='Day', y_title="d'", template='simple_white', expert_line=False, chance=False,
                                   transition_color=['black', 'black', 'black'])
fig.show()

In [59]:
behav = pd.read_feather('../../../MultiCon_AfterHours/MultiCon_EEG1/output/behav/mc_EEG1_02/mc_EEG1_02_A5.feat')
fig = pf.plot_lick_raster(behav, titles=[''], x_title='Linearized Position (rad)', y_title='Trial', font_size=22)
fig.update_layout(title={
    'text': 'Lick Raster',
    'y':0.9,
    'x':0.5,
    'xanchor': 'center',
    'yanchor': 'top'})
fig.show()
fig.write_image(os.path.join(fig_path, 'lick_raster_day5.png'))

In [58]:
fig = pf.custom_graph_template(y_title='Linearized Position (rad)', x_title='Time (s)', height=500, width=700, font_size=22)
fig.add_trace(go.Scatter(x=behav['t'], y=behav['lin_position'], mode='lines', line_color='darkgrey'))
fig.update_layout(title={
    'text': 'Linearized Position',
    'y':0.9,
    'x':0.5,
    'xanchor': 'center',
    'yanchor': 'top'})
fig.show()
fig.write_image(pjoin(fig_path, 'lin_pos.png'))

In [ ]:
fig = pf.plot_circle_position(behav, x_title='Position (x)', y_title='Position (y)')
fig.show()

In [ ]:
## Plot for days to criteria vs percent overlap
## This is not how I will do this in the future, just need this for proposal
performance_dict = {'mc_EEG1_01': {'days': [5, 5, 2], 'overlap': [27.55, 53.61, 52.48]},
                    'mc_EEG1_02': {'days': [5, 2], 'overlap': [40.62, 51.94]}}
df = pd.DataFrame(performance_dict)
y_data = np.concatenate((df.loc['days', 'mc_EEG1_01'], df.loc['days', 'mc_EEG1_02']))
x_data = np.concatenate((df.loc['overlap', 'mc_EEG1_01'], df.loc['overlap', 'mc_EEG1_02']))
lm = pg.linear_regression(X=x_data, y=y_data, as_dataframe=False)
lm_x = []
for n in np.arange(len(lm['X'])):
    lm_x.append(lm['X'][n][1])
colors = ['darkgrey', 'turquoise']
fig = pf.custom_graph_template(x_title='Neuronal Overlap (%)', y_title='Days to Criteria', font_size=14)
for idx, mouse in enumerate(df.columns):    
    fig.add_trace(go.Scatter(x=df.loc['overlap', mouse], y=df.loc['days', mouse], 
                             mode='markers', marker=dict(color=colors[idx]), name=mouse))
fig.add_trace(go.Scatter(x=lm_x, y=lm['pred'], mode='lines', line_color='turquoise', showlegend=False))
fig.show()
# fig.write_image(pjoin(fig_path, 'days_to_vs_overlap.png'))

In [60]:
## Plot for days to criteria vs percent overlap
## This is not how I will do this in the future, just need this for proposal
performance_dict = {'mc_EEG1_01': {'days': [5, 5, 2], 'overlap': [27.55, 53.61, 52.48]},
                    'mc_EEG1_02': {'days': [5, 2], 'overlap': [40.62, 51.94]}}
df = pd.DataFrame(performance_dict)
y_data = np.concatenate((df.loc['days', 'mc_EEG1_01'], df.loc['days', 'mc_EEG1_02']))
x_data = np.concatenate((df.loc['overlap', 'mc_EEG1_01'], df.loc['overlap', 'mc_EEG1_02']))
lm = pg.linear_regression(X=x_data, y=y_data, as_dataframe=False)
lm_x = []
for n in np.arange(len(lm['X'])):
    lm_x.append(lm['X'][n][1])
colors = ['darkgrey', 'turquoise']
fig = pf.custom_graph_template(x_title='Neuronal Overlap (%)', y_title='Days to Criteria', font_size=22)
for idx, mouse in enumerate(df.columns):    
    fig.add_trace(go.Scatter(x=df.loc['overlap', mouse], y=df.loc['days', mouse], 
                             mode='markers', marker=dict(color='black'), opacity=0.8, showlegend=False))
fig.add_trace(go.Scatter(x=lm_x, y=lm['pred'], mode='lines', line_color='turquoise', showlegend=False))
fig.show()
fig.write_image(pjoin(fig_path, 'days_to_vs_overlap.png'))

In [ ]:
pg.corr(x=x_data, y=y_data, method='spearman')

In [ ]:
## Power analysis for specific aim 1
## since n is not given as an argument, calculates the n value needed to achieve 80% power
f'n = {pg.power_corr(r=-0.5, power=0.8, alpha=0.05)}'

### Combine young mice with middle-aged mice from MultiCon_Aging1 data

In [ ]:
## Get days to 75% for each young mouse
days_to_dict = {'mouse': ['mc_EEG1_01', 'mc_EEG1_02', 'mc_EEG2_02'],
                'A': [5, 4, 5],
                'B': [5, 5, 5],
                'C': [5, 2, 2],
                'D': [2, 1, 2]}
df = pd.DataFrame(days_to_dict)
melt_df = df.melt(id_vars=['mouse'], 
                  value_vars=['A', 'B', 'C', 'D'],
                  var_name='context',
                  value_name='days_to')
avg_days = melt_df.groupby(['context'], as_index=False, sort=False).agg({'days_to': ['mean', 'sem']})
avg_days_df = pd.concat((avg_days['context'], avg_days['days_to']), axis=1)

## Aged mice
combined_dict = {'mouse': ['mca01', 'mca23', 'mca20'],
                'A': [8, 7, 6],
                'B': [1, 4, 7],
                'C': [3, 7, 7],
                'D': [11, 2, 23]}
df_aged = pd.DataFrame(combined_dict)
melt_df_aged = df_aged.melt(id_vars=['mouse'], 
                  value_vars=['A', 'B', 'C', 'D'],
                  var_name='context',
                  value_name='days_to')
avg_days = melt_df_aged.groupby(['context'], as_index=False, sort=False).agg({'days_to': ['mean', 'sem']})
aged_avg = pd.concat((avg_days['context'], avg_days['days_to']), axis=1)
## Plot
fig = pf.custom_graph_template(x_title='', y_title='', titles=['Young Adult Mice', 'Middle-Aged Mice'], 
                               rows=1, columns=2, shared_y=True, width=600, font_size=22)
## Young
fig.add_trace(go.Scatter(x=avg_days_df['context'], y=avg_days_df['mean'],
                            mode='lines+markers',
                            error_y=dict(type='data', array=avg_days_df['sem']),
                            line=dict(color='turquoise'), showlegend=False), row=1, col=1)
for mouse in np.unique(days_to_dict['mouse']):
    sub = melt_df[melt_df['mouse'] == mouse]
    fig.add_trace(go.Scatter(x=sub['context'], y=sub['days_to'],
                            mode='lines',
                            line=dict(color='darkgrey'), 
                            showlegend=False,
                            line_width=0.5), row=1, col=1)
## Middle aged
fig.add_trace(go.Scatter(x=aged_avg['context'], y=aged_avg['mean'],
                            mode='lines+markers',
                            error_y=dict(type='data', array=aged_avg['sem']),
                            line=dict(color='darkgrey'), showlegend=False), row=1, col=2)
for mouse in np.unique(combined_dict['mouse']):
    sub = melt_df_aged[melt_df_aged['mouse'] == mouse]
    fig.add_trace(go.Scatter(x=sub['context'], y=sub['days_to'],
                            mode='lines',
                            line=dict(color='darkgrey'), 
                            showlegend=False,
                            line_width=0.5), row=1, col=2)
fig.update_annotations(font_size=22)
fig.update_yaxes(title = 'Days to Criteria', row=1, col=1)
fig.show()
# fig.write_image(pjoin(fig_path, 'young_aged_daysto75.png'))

In [ ]:
## Get days to 75% for each young mouse for AD R01
## Changed B, C, D keys to A, B, C in days_to_dict and removed the orignial A key
days_to_dict = {'mouse': ['mc_EEG1_01', 'mc_EEG1_02', 'mc_EEG2_02'],
                'A': [5, 5, 5],
                'B': [5, 2, 2],
                'C': [2, 1, 2]}
df = pd.DataFrame(days_to_dict)
melt_df = df.melt(id_vars=['mouse'], 
                  value_vars=['A', 'B', 'C'],
                  var_name='context',
                  value_name='days_to')
avg_days = melt_df.groupby(['context'], as_index=False, sort=False).agg({'days_to': ['mean', 'sem']})
avg_days_df = pd.concat((avg_days['context'], avg_days['days_to']), axis=1)

## Aged mice
combined_dict = {'mouse': ['mca01', 'mca23', 'mca20'],
                'A': [1, 4, 7],
                'B': [3, 7, 7],
                'C': [11, 2, 23]}
df_aged = pd.DataFrame(combined_dict)
melt_df_aged = df_aged.melt(id_vars=['mouse'], 
                  value_vars=['A', 'B', 'C'],
                  var_name='context',
                  value_name='days_to')
avg_days = melt_df_aged.groupby(['context'], as_index=False, sort=False).agg({'days_to': ['mean', 'sem']})
aged_avg = pd.concat((avg_days['context'], avg_days['days_to']), axis=1)
## Plot
fig = pf.custom_graph_template(x_title='', y_title='', titles=['Young Adult Mice', 'Middle-Aged Mice'], 
                               rows=1, columns=2, shared_y=True, width=600, font_size=22)
## Young
fig.add_trace(go.Scatter(x=avg_days_df['context'], y=avg_days_df['mean'],
                            mode='lines+markers',
                            error_y=dict(type='data', array=avg_days_df['sem']),
                            line=dict(color='turquoise'), showlegend=False), row=1, col=1)
for mouse in np.unique(days_to_dict['mouse']):
    sub = melt_df[melt_df['mouse'] == mouse]
    fig.add_trace(go.Scatter(x=sub['context'], y=sub['days_to'],
                            mode='lines',
                            line=dict(color='darkgrey'), 
                            showlegend=False,
                            line_width=0.5), row=1, col=1)
## Middle aged
fig.add_trace(go.Scatter(x=aged_avg['context'], y=aged_avg['mean'],
                            mode='lines+markers',
                            error_y=dict(type='data', array=aged_avg['sem']),
                            line=dict(color='darkgrey'), showlegend=False), row=1, col=2)
for mouse in np.unique(combined_dict['mouse']):
    sub = melt_df_aged[melt_df_aged['mouse'] == mouse]
    fig.add_trace(go.Scatter(x=sub['context'], y=sub['days_to'],
                            mode='lines',
                            line=dict(color='darkgrey'), 
                            showlegend=False,
                            line_width=0.5), row=1, col=2)
fig.update_annotations(font_size=22)
fig.update_yaxes(title = 'Days to Criteria', row=1, col=1)
fig.show()
fig.write_image(pjoin(fig_path, 'days_to_criteria_AD_R01.png'))

In [ ]:
## Sphericity young
pg.sphericity(data=melt_df, dv='days_to', within='context', subject='mouse')

In [ ]:
## Young rm-anova
melt_df.rm_anova(dv='days_to', within='context', subject='mouse', detailed=True)

In [ ]:
## Sphericity middle-aged
pg.sphericity(data=melt_df_aged, dv='days_to', within='context', subject='mouse')

In [ ]:
## Middle-aged rm-anova
melt_df_aged.rm_anova(dv='days_to', within='context', subject='mouse', detailed=True)

In [ ]:
## Two way rm anova
melt_df['age'] = 'Y'
melt_df_aged['age'] = 'MA'
melt_combined = pd.concat([melt_df, melt_df_aged], axis=0)

In [ ]:
pg.mixed_anova(data=melt_combined, between='age', within='context', dv='days_to', subject='mouse')

In [ ]:
## One-way RM ANOVA power analysis
pg.power_rm_anova(eta_squared=0.37, m=3, power=0.9)

## Testing for place cell code below.

In [ ]:
fpath = '../../../MultiCon_AfterHours/MultiCon_EEG1/output/rotated_placefields/mc_EEG1_01/'
rotation_df = pd.read_feather(pjoin(fpath, 'A1_A5_placecells_pearson.feat'))
test = rotation_df.groupby(['mouse', 'session', 'rotation'], as_index=False).agg({'r': ['mean', 'sem']})
test_df = pd.concat([test['mouse'], test['session'], test['rotation'], test['r']], axis=1)
fig_data = test_df
specs = [[{'type': 'polar'}, {'type': 'polar'}, {'type': 'polar'}, {'type': 'polar'}, {'type': 'polar'}]]
fig = pf.custom_graph_template(x_title='', y_title='', font_size=11, rows=1, columns=5, 
                               width=1600, height=400, specs=specs)
for idx, session in enumerate(np.unique(fig_data['session'])):
    fig.add_trace(go.Barpolar(
        r=fig_data['mean'][fig_data['session'] == session],
        theta=fig_data['rotation'][fig_data['session'] == session],
        marker_color='turquoise',
        marker_line_color='black',
        marker_line_width=1,
        opacity=0.8,
        showlegend=False
    ), row=1, col=idx + 1)
    
fig.update_polars(
        radialaxis = dict(showticklabels=True, ticks='', angle=180, tickangle=-180, range=[-0.2, 1], showgrid=True, gridcolor='darkgrey'),
        angularaxis = dict(showticklabels=True, ticks='', showgrid=True, gridcolor='darkgrey')
    )
fig.show()
fig.write_image(pjoin(fig_path, 'A1_A5_placecells.png'))

In [ ]:
fpath = '../../../MultiCon_AfterHours/MultiCon_EEG1/output/rotated_placefields/mc_EEG1_01/'
rotation_df = pd.read_feather(pjoin(fpath, 'B1_B5_placecells_pearson.feat'))
test = rotation_df.groupby(['mouse', 'session', 'rotation'], as_index=False).agg({'r': ['mean', 'sem']})
test_df = pd.concat([test['mouse'], test['session'], test['rotation'], test['r']], axis=1)
fig_data = test_df
specs = [[{'type': 'polar'}, {'type': 'polar'}, {'type': 'polar'}, {'type': 'polar'}, {'type': 'polar'}]]
fig = pf.custom_graph_template(x_title='', y_title='', font_size=11, rows=1, columns=5, 
                               width=1600, height=400, specs=specs)
for idx, session in enumerate(np.unique(fig_data['session'])):
    fig.add_trace(go.Barpolar(
        r=fig_data['mean'][fig_data['session'] == session],
        theta=fig_data['rotation'][fig_data['session'] == session],
        marker_color='orange',
        marker_line_color='black',
        marker_line_width=1,
        opacity=0.8,
        showlegend=False
    ), row=1, col=idx + 1)
    
fig.update_polars(
        radialaxis = dict(showticklabels=True, ticks='', angle=180, tickangle=-180, range=[-0.2, 1], showgrid=True, gridcolor='darkgrey'),
        angularaxis = dict(showticklabels=True, ticks='', showgrid=True, gridcolor='darkgrey')
    )
fig.show()
fig.write_image(pjoin(fig_path, 'B1_B5_placecells.png'))